# SA coding assessment: Data Engineering, Baby Names
## Version 2022.02

What you'll do:
* We provide the dataset. You will load it into dataframes, and perform some data cleansing and transformation tasks.
* You will answer a series of questions to show insights from the data.
* There are also some written-answer questions.

*We care about the process, not the result.*  I.e., we're looking for proper use of data engineering techniques and understanding of the code you've written.  

This Data Engineering section is scored out of 50 points.

In [0]:
# This folder is for you to write any data as needed. Write access is restricted elsewhere. You can always read from dbfs.
aws_role_id = "AROAUQVMTFU2DCVUR57M2"
user = dbutils.notebook.entry_point.getDbutils().notebook().getContext().tags().apply('user')
userhome = f"s3a://e2-interview-user-data/home/{aws_role_id}:{user}"
print(userhome)
print(user)

s3a://e2-interview-user-data/home/AROAUQVMTFU2DCVUR57M2:rashiranjith@gmail.com
rashiranjith@gmail.com


## Using Baby Names Data Set

This dataset comes from a website referenced by [Data.gov](http://catalog.data.gov/dataset/baby-names-beginning-2007). It lists baby names used in the state of NY from 2007 to 2018.

Run the following two cells to copy this file to a usable location.

In [0]:
%scala

import java.net.URL
import java.io.File
import org.apache.commons.io.FileUtils

val tmpFile = new File("/tmp/rows.json")
FileUtils.copyURLToFile(new URL("https://health.data.ny.gov/api/views/jxy9-yhdk/rows.json?accessType=DOWNLOAD"), tmpFile)

import java.net.URL
import java.io.File
import org.apache.commons.io.FileUtils
tmpFile: java.io.File = /tmp/rows.json

In [0]:
# https://docs.python.org/3/library/hashlib.html#blake2
from hashlib import blake2b

user = dbutils.notebook.entry_point.getDbutils().notebook().getContext().tags().apply('user')
h = blake2b(digest_size=4)
h.update(user.encode("utf-8"))
display_name = "user_" + h.hexdigest()
print("Display Name: " + display_name)

# dbutils.fs.cp('file:/tmp/rows.json', userhome + '/rows.json')
# dbutils.fs.cp(userhome + '/rows.json' ,f"dbfs:/tmp/{display_name}/rows.json")
dbutils.fs.cp('file:/tmp/rows.json',f"dbfs:/tmp/{display_name}/rows.json")
baby_names_path = f"dbfs:/tmp/{display_name}/rows.json"

print("Baby Names Path: " + baby_names_path)
dbutils.fs.head(baby_names_path)

# Ensure you use baby_names_path to answer the questions. A bug in Spark 2.X will cause your read to fail if you read the file from userhome. 
# Please note that dbfs:/tmp is cleaned up daily at 6AM pacific

Display Name: user_bbfa5ce0
Baby Names Path: dbfs:/tmp/user_bbfa5ce0/rows.json
[Truncated to first 65536 bytes]


'{\n  "meta" : {\n    "view" : {\n      "id" : "jxy9-yhdk",\n      "name" : "Baby Names: Beginning 2007",\n      "assetType" : "dataset",\n      "attribution" : "New York State Department of Health",\n      "attributionLink" : "http://www.health.ny.gov/statistics/vital_statistics/",\n      "averageRating" : 0,\n      "category" : "Health",\n      "createdAt" : 1356724562,\n      "description" : "New York State Baby Names are aggregated and displayed by the year, county, or borough where the mother resided as stated on a New York State or New York City (NYC) birth certificate. The frequency of the baby name is listed if there are 5 or more of the same baby name in a county outside of NYC or 10 or more of the same baby name in a NYC borough.",\n      "displayType" : "table",\n      "downloadCount" : 120682,\n      "hideFromCatalog" : false,\n      "hideFromDataJson" : false,\n      "newBackend" : true,\n      "numberOfComments" : 0,\n      "oid" : 40162507,\n      "provenance" : "officia

#### Baby Names Question 1 - Nested Data [15 Points]


Use Spark SQL's native JSON support to read the baby names file into a dataframe. Use this dataframe to create a temporary table containing all the nested data columns ("sid", "id", "position", "created_at", "created_meta", "updated_at", "updated_meta", "meta", "year", "first_name", "county", "sex", "count") so that they can be queried using SQL. 

Hint: you can use ```dbutils.fs.head(baby_names_path)``` to take a look at the dataset before reading it in. 

Suggested Steps:
1. Read in the JSON data
2. Pull all columns in the nested data column to top level, following the schema specified above. There are [built-in Spark SQL functions](https://spark.apache.org/docs/latest/api/sql/index.html) that will accomplish this.
3. Create a temp table from this expanded dataframe using createOrReplaceTempView()

In [0]:
from pyspark.sql.functions import col, explode
df = spark.read.option("multiLine", "true").json(baby_names_path).cache()
# df.show()


# Explode the 'data' array to transform it into individual rows
exploded_df = df.select(explode(col("data")).alias("data"))
# exploded_df.show()
flattened_df = exploded_df.select(
    col("data")[0].alias("sid"),
    col("data")[1].alias("id"),
    col("data")[2].alias("position"),
    col("data")[3].alias("created_at"),
    col("data")[4].alias("created_meta"),
    col("data")[5].alias("updated_at"),
    col("data")[6].alias("updated_meta"),
    col("data")[7].alias("meta"),
    col("data")[8].alias("year"),
    col("data")[9].alias("first_name"),
    col("data")[10].alias("county"),
    col("data")[11].alias("sex"),
    col("data")[12].alias("count")
)

# Show the flattened DataFrame
# flattened_df.show()
flattened_df.createOrReplaceTempView("baby_names")

In [0]:
%sql
select * from baby_names limit 10;

sid id position created_at created_meta updated_at updated_meta meta year first_name county sex count row-v6cf~i865.pzhn 00000000-0000-0000-A0DB-E84F4D18323D 0 1699650491 null 1699650491 null { } 2021 OLIVIA Albany F 16 row-i6yp_z5f6_3gyd 00000000-0000-0000-1150-24582DCADD0A 0 1699650491 null 1699650491 null { } 2021 AMELIA Albany F 16 row-wfh4-5veb.96wi 00000000-0000-0000-DB51-422E20326A7C 0 1699650491 null 1699650491 null { } 2021 SOPHIA Albany F 13 row-kh94.hvkq-ssiz 00000000-0000-0000-73B7-70099BDE7DB0 0 1699650491 null 1699650491 null { } 2021 AVA Albany F 13 row-teme.x694~r6jk 00000000-0000-0000-8D30-76A2E60F8943 0 1699650491 null 1699650491 null { } 2021 EMMA Albany F 12 row-bbsc.xej2_sgp9 00000000-0000-0000-BA42-6B7EA6BCE0F6 0 1699650491 null 1699650491 null { } 2021 PENELOPE Albany F 11 row-iekm-y8iv.uhy9 00000000-0000-0000-A6F0-521B7E01965B 0 1699650491 null 1699650491 null { } 2021 MADISON Albany F 10 row-bqth.4bfp_2xg4 00000000-0000-0000-FB59-F1D76944350E 0 1699650491 null 1699650491 null { } 2021 ABIGAIL Albany F 10 row-a2fc-g57s_wg4v 00000000-0000-0000-E027-45EA5671EDC9 0 1699650491 null 1699650491 null { } 2021 HARPER Albany F 10 row-7mwd~364p.wfau 00000000-0000-0000-A4E4-09DDAE8BB85D 0 1699650491 null 1699650491 null { } 2021 ISLA Albany F 9

In [0]:
%sql

SELECT year, first_name, count
FROM (
    SELECT year, first_name, count,
           RANK() OVER (PARTITION BY year ORDER BY count DESC) as rank
    FROM baby_names
) ranked
WHERE rank = 1


year first_name count 2007 JOHN 99 2007 JAKE 99 2008 JEREMIAH 99 2008 MATTHEW 99 2009 JACK 99 2009 SOPHIA 99 2009 MADISON 99 2010 CHAIM 99 2010 JUSTIN 99 2010 LOGAN 99 2011 GABRIEL 99 2011 JAYDEN 99 2011 JOSHUA 99 2011 MENACHEM 99 2011 MIA 99 2011 AARON 99 2012 JASON 99 2012 MADISON 99 2013 JAMES 99 2013 AARON 99 2013 DYLAN 99 2014 JOSHUA 99 2014 JAMES 99 2015 LOGAN 99 2015 SOPHIA 99 2016 MATTHEW 99 2016 MATTHEW 99 2016 ANTHONY 99 2017 DYLAN 99 2018 ABIGAIL 99 2018 OLIVIA 99 2018 LUCAS 99 2019 JAMES 99 2019 ANTHONY 99 2020 RIVKA 96 2020 YOSEF 96 2020 DYLAN 96 2021 OLIVIA 99 2021 EMMA 99

In [0]:
from pyspark.sql.window import Window
from pyspark.sql.functions import col, rank

# Define a window spec partitioned by year and ordered by count in descending order
windowSpec = Window.partitionBy("year").orderBy(col("count").desc())

# Use the rank function over the window spec
ranked_df = flattened_df.withColumn("rank", rank().over(windowSpec))

# Filter for the top-ranked names in each year
most_popular_names_df = ranked_df.filter(col("rank") == 1).select("year", "first_name", "count")

# Show the result
most_popular_names_df.show()

+----+----------+-----+
|year|first_name|count|
+----+----------+-----+
|2007|      JOHN|   99|
|2007|      JAKE|   99|
|2008|  JEREMIAH|   99|
|2008|   MATTHEW|   99|
|2009|      JACK|   99|
|2009|    SOPHIA|   99|
|2009|   MADISON|   99|
|2010|     CHAIM|   99|
|2010|    JUSTIN|   99|
|2010|     LOGAN|   99|
|2011|   GABRIEL|   99|
|2011|    JAYDEN|   99|
|2011|    JOSHUA|   99|
|2011|  MENACHEM|   99|
|2011|       MIA|   99|
|2011|     AARON|   99|
|2012|     JASON|   99|
|2012|   MADISON|   99|
|2013|     JAMES|   99|
|2013|     AARON|   99|
+----+----------+-----+
only showing top 20 rows



In [0]:
%scala

import java.net.URL
import java.io.File
import org.apache.commons.io.FileUtils
val tmpFileVisitors = new File("/tmp/visitors.json")
FileUtils.copyURLToFile(new URL("https://raw.githubusercontent.com/jservin/public-scratch-pad/master/births-with-visitor-data.json?accessType=DOWNLOAD"), tmpFileVisitors)



import java.net.URL
import java.io.File
import org.apache.commons.io.FileUtils
tmpFileVisitors: java.io.File = /tmp/visitors.json

In [0]:
# https://docs.python.org/3/library/hashlib.html#blake2
from hashlib import blake2b

user = dbutils.notebook.entry_point.getDbutils().notebook().getContext().tags().apply('user')
h = blake2b(digest_size=4)
h.update(user.encode("utf-8"))
display_name = "user_" + h.hexdigest()
print("Display Name: " + display_name)

dbutils.fs.cp('file:/tmp/visitors.json',f"dbfs:/tmp/{display_name}/visitors.json")
visitors_path = f"dbfs:/tmp/{display_name}/visitors.json"

print("Visotrs Path: " + visitors_path)
dbutils.fs.head(visitors_path)

Display Name: user_bbfa5ce0
Visotrs Path: dbfs:/tmp/user_bbfa5ce0/visitors.json
[Truncated to first 65536 bytes]


'{"sid":"row-r9pv-p86t.ifsp","id":"00000000-0000-0000-0838-60C2FFCC43AE","position":"0","created_at":"1574264158","updated_at":"1574264158","meta":"{ }","year":"2007","first_name":"ZOEY","county":"KINGS","sex":"F","name_count":"11","visitors":"<?xml version=\\"1.0\\" encoding=\\"utf-8\\"?>\\n  <visitors>\\n    <visitor id=\\"9615\\" age=\\"68\\" sex=\\"F\\" />\\n    <visitor id=\\"1882\\" age=\\"34\\" sex=\\"M\\" />\\n    <visitor id=\\"5987\\" age=\\"23\\" sex=\\"M\\" />\\n  </visitors>"}\n{"sid":"row-7v2v~88z5-44se","id":"00000000-0000-0000-C8FC-DDD3F9A72DFF","position":"0","created_at":"1574264158","updated_at":"1574264158","meta":"{ }","year":"2007","first_name":"ZOEY","county":"SUFFOLK","sex":"F","name_count":"6","visitors":"<?xml version=\\"1.0\\" encoding=\\"utf-8\\"?>\\n  <visitors>\\n    <visitor id=\\"3230\\" age=\\"45\\" sex=\\"M\\" />\\n    <visitor id=\\"5243\\" age=\\"44\\" sex=\\"M\\" />\\n  </visitors>"}\n{"sid":"row-hzc9-4kvv~mbc9","id":"00000000-0000-0000-562E-D9A0792

In [0]:
df_visitors = spark.read.option("inferSchema", True).json(visitors_path)

In [0]:
# Select and show only the 'visitors' column
df_visitors.select("visitors").limit(1).show(truncate=False)

+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
|visitors                                                                                                                                                                                               |
+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
|<?xml version="1.0" encoding="utf-8"?>\n  <visitors>\n    <visitor id="9615" age="68" sex="F" />\n    <visitor id="1882" age="34" sex="M" />\n    <visitor id="5987" age="23" sex="M" />\n  </visitors>|
+-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [0]:
import xml.etree.ElementTree as ET
from pyspark.sql.functions import udf
from pyspark.sql.types import StringType, StructType, StructField  # Import additional types as needed

def parse_visitors(xml_data):
    if xml_data is None or xml_data.strip() == '':
        return []

    try:
        visitors = []
        root = ET.fromstring(xml_data)

        for visitor in root.findall('visitor'):
            visitor_id = visitor.get('id')
            visitor_age = int(visitor.get('age')) if visitor.get('age') is not None else None
            visitor_sex = visitor.get('sex')

            visitors.append((visitor_id, visitor_age, visitor_sex))

        return visitors
    except ET.ParseError:
        return []  # Return empty list in case of parsing error

# Define the schema for the visitor information
visitor_schema = ArrayType(StructType([
    StructField("id", StringType(), True),
    StructField("age", IntegerType(), True),
    StructField("sex", StringType(), True)
]))

# Register the UDF
parse_visitors_udf = udf(parse_visitors, visitor_schema)


In [0]:
df_visitors_transformed = df_visitors.withColumn("parsed_visitors", parse_visitors_udf(df_visitors["visitors"]))

In [0]:
df_visitors_transformed.select('county','created_at','first_name','id','meta','name_count','position','sex','sid','updated_at','year','parsed_visitors').limit(1).show(truncate=False)

+------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+---------------------------------------------+
|county|created_at|first_name|id                                  |meta|name_count|position|sex|sid               |updated_at|year|parsed_visitors                              |
+------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+---------------------------------------------+
|KINGS |1574264158|ZOEY      |00000000-0000-0000-0838-60C2FFCC43AE|{ } |11        |0       |F  |row-r9pv-p86t.ifsp|1574264158|2007|[{9615, 68, F}, {1882, 34, M}, {5987, 23, M}]|
+------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+---------------------------------------------+



In [0]:
df_visitors_flattened = df_visitors_transformed.withColumn("visitor", explode("parsed_visitors"))

In [0]:
df_visitors_flattened.show(truncate=False)

+-----------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+----+----------------------------------------------------------+-------------+
|county     |created_at|first_name|id                                  |meta|name_count|position|sex|sid               |updated_at|visitors                                                                                                                                                                                                                                         |year|parsed_visitors                                           |visitor      |
+-----------+----------+----------+------------------------------------+----+----------+--------

In [0]:
df_visitors_flattened=df_visitors_flattened.select(
    "county",
    "created_at",
    "first_name",
    "id",
    "meta",
    "name_count",
    "position",
    "sex",
    "sid",
    "updated_at",
    "year",
    "visitor.id",
    "visitor.age",
    "visitor.sex"
)

In [0]:
df_visitors_flattened.show(truncate=False)

+-----------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+----+---+---+
|county     |created_at|first_name|id                                  |meta|name_count|position|sex|sid               |updated_at|year|id  |age|sex|
+-----------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+----+---+---+
|KINGS      |1574264158|ZOEY      |00000000-0000-0000-0838-60C2FFCC43AE|{ } |11        |0       |F  |row-r9pv-p86t.ifsp|1574264158|2007|9615|68 |F  |
|KINGS      |1574264158|ZOEY      |00000000-0000-0000-0838-60C2FFCC43AE|{ } |11        |0       |F  |row-r9pv-p86t.ifsp|1574264158|2007|1882|34 |M  |
|KINGS      |1574264158|ZOEY      |00000000-0000-0000-0838-60C2FFCC43AE|{ } |11        |0       |F  |row-r9pv-p86t.ifsp|1574264158|2007|5987|23 |M  |
|SUFFOLK    |1574264158|ZOEY      |00000000-0000-0000-C8FC-DDD3F9A72DFF|{ } |6         |0       |F  

In [0]:
# Filter the DataFrame for first_name 'ZOEY' and year 2007
filtered_df = df_visitors_flattened.filter((df_visitors_flattened['first_name'] == 'ZOEY') & (df_visitors_flattened['year'] == 2007))

# Show the result
filtered_df.show(truncate=False)


+-------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+----+---+---+
|county |created_at|first_name|id                                  |meta|name_count|position|sex|sid               |updated_at|year|id  |age|sex|
+-------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+----+---+---+
|KINGS  |1574264158|ZOEY      |00000000-0000-0000-0838-60C2FFCC43AE|{ } |11        |0       |F  |row-r9pv-p86t.ifsp|1574264158|2007|9615|68 |F  |
|KINGS  |1574264158|ZOEY      |00000000-0000-0000-0838-60C2FFCC43AE|{ } |11        |0       |F  |row-r9pv-p86t.ifsp|1574264158|2007|1882|34 |M  |
|KINGS  |1574264158|ZOEY      |00000000-0000-0000-0838-60C2FFCC43AE|{ } |11        |0       |F  |row-r9pv-p86t.ifsp|1574264158|2007|5987|23 |M  |
|SUFFOLK|1574264158|ZOEY      |00000000-0000-0000-C8FC-DDD3F9A72DFF|{ } |6         |0       |F  |row-7v2v~88z5-44se|15742641

In [0]:
# Filter the DataFrame for first_name 'ZOEY' and year 2007
# filtered_df = df_visitors_flattened.filter((df_visitors_flattened['first_name'] == 'ZOEY') & (df_visitors_flattened['year'] == 2007))

filtered_df = df_visitors.filter((df_visitors['first_name'] == 'ZOEY') & (df_visitors['year'] == 2007))

# Show the result
filtered_df.show(truncate=False)

+-------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+----+
|county |created_at|first_name|id                                  |meta|name_count|position|sex|sid               |updated_at|visitors                                                                                                                                                                                               |year|
+-------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+----+
|

In [0]:
# https://docs.python.org/3/library/hashlib.html#blake2
from hashlib import blake2b

user = dbutils.notebook.entry_point.getDbutils().notebook().getContext().tags().apply('user')
h = blake2b(digest_size=4)
h.update(user.encode("utf-8"))
display_name = "user_" + h.hexdigest()
print("Display Name: " + display_name)

dbutils.fs.cp('file:/tmp/visitors.json',f"dbfs:/tmp/{display_name}/visitors.json")
visitors_path = f"dbfs:/tmp/{display_name}/visitors.json"

print("Visotrs Path: " + visitors_path)
dbutils.fs.head(visitors_path)


df_visitors = spark.read.option("inferSchema", True).json(visitors_path)


import xml.etree.ElementTree as ET
from pyspark.sql.functions import udf
from pyspark.sql.types import StringType, StructType, StructField  # Import additional types as needed

def parse_visitors(xml_data):
    if xml_data is None or xml_data.strip() == '':
        return []

    try:
        visitors = []
        root = ET.fromstring(xml_data)

        for visitor in root.findall('visitor'):
            visitor_id = visitor.get('id')
            visitor_age = int(visitor.get('age')) if visitor.get('age') is not None else None
            visitor_sex = visitor.get('sex')

            visitors.append((visitor_id, visitor_age, visitor_sex))

        return visitors
    except ET.ParseError:
        return []  # Return empty list in case of parsing error

# Define the schema for the visitor information
visitor_schema = ArrayType(StructType([
    StructField("id", StringType(), True),
    StructField("age", IntegerType(), True),
    StructField("sex", StringType(), True)
]))

# Register the UDF
parse_visitors_udf = udf(parse_visitors, visitor_schema)


df_visitors_transformed = df_visitors.withColumn("parsed_visitors", parse_visitors_udf(df_visitors["visitors"]))


df_visitors_transformed.select('county','created_at','first_name','id','meta','name_count','position','sex','sid','updated_at','year','parsed_visitors').limit(1).show(truncate=False)


df_visitors_flattened = df_visitors_transformed.withColumn("visitor", explode("parsed_visitors"))


df_visitors_flattened=df_visitors_flattened.select(
    "county",
    "created_at",
    "first_name",
    "id",
    "meta",
    "name_count",
    "position",
    "sex",
    "sid",
    "updated_at",
    "year",
    "visitor.id",
    "visitor.age",
    "visitor.sex"
)

df_visitors_flattened.show(truncate=False)

Display Name: user_bbfa5ce0
Visotrs Path: dbfs:/tmp/user_bbfa5ce0/visitors.json
[Truncated to first 65536 bytes]
+------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+---------------------------------------------+
|county|created_at|first_name|id                                  |meta|name_count|position|sex|sid               |updated_at|year|parsed_visitors                              |
+------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+---------------------------------------------+
|KINGS |1574264158|ZOEY      |00000000-0000-0000-0838-60C2FFCC43AE|{ } |11        |0       |F  |row-r9pv-p86t.ifsp|1574264158|2007|[{9615, 68, F}, {1882, 34, M}, {5987, 23, M}]|
+------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+--------------------------------------------

In [0]:
print(df_visitors_flattened)

DataFrame[county: string, created_at: string, first_name: string, id: string, meta: string, name_count: string, position: string, sex: string, sid: string, updated_at: string, year: string, id: string, age: int, sex: string]


In [0]:
from pyspark.sql.functions import col, countDistinct

# Group by the 'county' column and count distinct values
distinct_counties = df_visitors_flattened.groupBy("county").agg(countDistinct("county").alias("distinct_counties"))

# Show the result
distinct_counties.show(truncate=False)


+----------+-----------------+
|county    |distinct_counties|
+----------+-----------------+
|FRANKLIN  |1                |
|STEUBEN   |1                |
|MONROE    |1                |
|LIVINGSTON|1                |
|ONONDAGA  |1                |
|NEW YORK  |1                |
|KINGS     |1                |
|ALBANY    |1                |
|WAYNE     |1                |
|MADISON   |1                |
|RICHMOND  |1                |
|ORANGE    |1                |
|CAYUGA    |1                |
|SUFFOLK   |1                |
|OTSEGO    |1                |
|OSWEGO    |1                |
|CLINTON   |1                |
|ERIE      |1                |
|BROOME    |1                |
|GREENE    |1                |
+----------+-----------------+
only showing top 20 rows



In [0]:
distinct_counties.show(121,truncate=False)

+------------+-----------------+
|county      |distinct_counties|
+------------+-----------------+
|FRANKLIN    |1                |
|STEUBEN     |1                |
|MONROE      |1                |
|LIVINGSTON  |1                |
|ONONDAGA    |1                |
|NEW YORK    |1                |
|KINGS       |1                |
|ALBANY      |1                |
|WAYNE       |1                |
|MADISON     |1                |
|RICHMOND    |1                |
|ORANGE      |1                |
|CAYUGA      |1                |
|SUFFOLK     |1                |
|OTSEGO      |1                |
|OSWEGO      |1                |
|CLINTON     |1                |
|ERIE        |1                |
|BROOME      |1                |
|GREENE      |1                |
|DELAWARE    |1                |
|NIAGARA     |1                |
|WYOMING     |1                |
|CHAUTAUQUA  |1                |
|ULSTER      |1                |
|TIOGA       |1                |
|YATES       |1                |
|SCHOHARIE

In [0]:
from pyspark.sql.functions import col, countDistinct, lower

# Convert 'county' values to lower case and count distinct values
# distinct_counties_lower = df_visitors_flattened.withColumn("county_lower", col("county").lower()) \
#                             .groupBy("county_lower") \
#                             .agg(countDistinct("county").alias("distinct_counties"))

distinct_counties_lower = df_visitors_flattened.withColumn('county_lower', col('county').upper()).groupBy('county_lower').agg(countDistinct('county').alias('distinct_counties'))

# Show the result
distinct_counties_lower.show(truncate=False)


---------------------------------------------------------------------------
TypeError                                 Traceback (most recent call last)
File <command-3155276111774451>, line 8
      1 from pyspark.sql.functions import col, countDistinct, lower
      3 # Convert 'county' values to lower case and count distinct values
      4 # distinct_counties_lower = df_visitors_flattened.withColumn("county_lower", col("county").lower()) \
      5 #                             .groupBy("county_lower") \
      6 #                             .agg(countDistinct("county").alias("distinct_counties"))
----> 8 distinct_counties_lower = df_visitors_flattened.withColumn('county_lower', col('county').upper()).groupBy('county_lower').agg(countDistinct('county').alias('distinct_counties'))
     10 # Show the result
     11 distinct_counties_lower.show(truncate=False)

TypeError: 'Column' object is not callable

In [0]:
from pyspark.sql.functions import col, countDistinct, upper

# Convert 'county' values to lower case and count distinct values
distinct_counties_lower = df_visitors_flattened.withColumn('county_lower', upper(col('county'))) \
                            .groupBy('county_lower') \
                            .agg(countDistinct('county').alias('distinct_counties'))

# Show the result
distinct_counties_lower.show(truncate=False)

+------------+-----------------+
|county_lower|distinct_counties|
+------------+-----------------+
|FULTON      |2                |
|ST. LAWRENCE|1                |
|CATTARAUGUS |2                |
|STEUBEN     |2                |
|YATES       |2                |
|KINGS       |2                |
|OSWEGO      |2                |
|MADISON     |2                |
|JEFFERSON   |2                |
|CHAUTAUQUA  |2                |
|SCHENECTADY |2                |
|WARREN      |2                |
|ROCKLAND    |2                |
|TIOGA       |2                |
|ALLEGANY    |2                |
|MONROE      |2                |
|SENECA      |2                |
|ONONDAGA    |2                |
|LEWIS       |2                |
|QUEENS      |2                |
+------------+-----------------+
only showing top 20 rows



In [0]:
from pyspark.sql.functions import col, countDistinct

# Group by the 'county' column and count distinct values
distinct_counties = df_visitors_flattened.groupBy("county").agg(countDistinct("county").alias("distinct_counties"))

# Show the result
# distinct_counties.show(truncate=False)

In [0]:
from pyspark.sql.functions import col, countDistinct, upper

# Convert 'county' values to lower case and count distinct values
distinct_counties_upper = df_visitors_flattened.withColumn('county_upper', upper(col('county'))) \
                            .groupBy('county_upper') \
                            .agg(countDistinct('county').alias('distinct_counties'))

# Show the result
distinct_counties_upper.show(truncate=False)

+------------+-----------------+
|county_upper|distinct_counties|
+------------+-----------------+
|FULTON      |2                |
|ST. LAWRENCE|1                |
|CATTARAUGUS |2                |
|STEUBEN     |2                |
|YATES       |2                |
|KINGS       |2                |
|OSWEGO      |2                |
|MADISON     |2                |
|JEFFERSON   |2                |
|CHAUTAUQUA  |2                |
|SCHENECTADY |2                |
|WARREN      |2                |
|ROCKLAND    |2                |
|TIOGA       |2                |
|ALLEGANY    |2                |
|MONROE      |2                |
|SENECA      |2                |
|ONONDAGA    |2                |
|LEWIS       |2                |
|QUEENS      |2                |
+------------+-----------------+
only showing top 20 rows



In [0]:
df_visitors_flattened.show(truncate=False)

+-----------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+----+---+---+
|county     |created_at|first_name|id                                  |meta|name_count|position|sex|sid               |updated_at|year|id  |age|sex|
+-----------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+----+---+---+
|KINGS      |1574264158|ZOEY      |00000000-0000-0000-0838-60C2FFCC43AE|{ } |11        |0       |F  |row-r9pv-p86t.ifsp|1574264158|2007|9615|68 |F  |
|KINGS      |1574264158|ZOEY      |00000000-0000-0000-0838-60C2FFCC43AE|{ } |11        |0       |F  |row-r9pv-p86t.ifsp|1574264158|2007|1882|34 |M  |
|KINGS      |1574264158|ZOEY      |00000000-0000-0000-0838-60C2FFCC43AE|{ } |11        |0       |F  |row-r9pv-p86t.ifsp|1574264158|2007|5987|23 |M  |
|SUFFOLK    |1574264158|ZOEY      |00000000-0000-0000-C8FC-DDD3F9A72DFF|{ } |6         |0       |F  

In [0]:
from pyspark.sql.functions import col, countDistinct, upper

# Convert 'county' values to lower case and count distinct values
df_visitors_flattened = df_visitors_flattened.withColumn('county_upper', upper(col('county'))) \
                            .groupBy('county_upper') \
                            .agg(countDistinct('county').alias('distinct_counties'))

# Show the result
df_visitors_flattened.show(truncate=False)

+------------+-----------------+
|county_upper|distinct_counties|
+------------+-----------------+
|FULTON      |2                |
|ST. LAWRENCE|1                |
|CATTARAUGUS |2                |
|STEUBEN     |2                |
|YATES       |2                |
|KINGS       |2                |
|OSWEGO      |2                |
|MADISON     |2                |
|JEFFERSON   |2                |
|CHAUTAUQUA  |2                |
|SCHENECTADY |2                |
|WARREN      |2                |
|ROCKLAND    |2                |
|TIOGA       |2                |
|ALLEGANY    |2                |
|MONROE      |2                |
|SENECA      |2                |
|ONONDAGA    |2                |
|LEWIS       |2                |
|QUEENS      |2                |
+------------+-----------------+
only showing top 20 rows



In [0]:
# https://docs.python.org/3/library/hashlib.html#blake2
from hashlib import blake2b

user = dbutils.notebook.entry_point.getDbutils().notebook().getContext().tags().apply('user')
h = blake2b(digest_size=4)
h.update(user.encode("utf-8"))
display_name = "user_" + h.hexdigest()
print("Display Name: " + display_name)

dbutils.fs.cp('file:/tmp/visitors.json',f"dbfs:/tmp/{display_name}/visitors.json")
visitors_path = f"dbfs:/tmp/{display_name}/visitors.json"

print("Visotrs Path: " + visitors_path)
dbutils.fs.head(visitors_path)


df_visitors = spark.read.option("inferSchema", True).json(visitors_path)


import xml.etree.ElementTree as ET
from pyspark.sql.functions import udf
from pyspark.sql.types import StringType, StructType, StructField  # Import additional types as needed

def parse_visitors(xml_data):
    if xml_data is None or xml_data.strip() == '':
        return []

    try:
        visitors = []
        root = ET.fromstring(xml_data)

        for visitor in root.findall('visitor'):
            visitor_id = visitor.get('id')
            visitor_age = int(visitor.get('age')) if visitor.get('age') is not None else None
            visitor_sex = visitor.get('sex')

            visitors.append((visitor_id, visitor_age, visitor_sex))

        return visitors
    except ET.ParseError:
        return []  # Return empty list in case of parsing error

# Define the schema for the visitor information
visitor_schema = ArrayType(StructType([
    StructField("id", StringType(), True),
    StructField("age", IntegerType(), True),
    StructField("sex", StringType(), True)
]))

# Register the UDF
parse_visitors_udf = udf(parse_visitors, visitor_schema)


df_visitors_transformed = df_visitors.withColumn("parsed_visitors", parse_visitors_udf(df_visitors["visitors"]))


df_visitors_transformed.select('county','created_at','first_name','id','meta','name_count','position','sex','sid','updated_at','year','parsed_visitors').limit(1).show(truncate=False)


df_visitors_flattened = df_visitors_transformed.withColumn("visitor", explode("parsed_visitors"))


df_visitors_flattened=df_visitors_flattened.select(
    "county",
    "created_at",
    "first_name",
    "id",
    "meta",
    "name_count",
    "position",
    "sex",
    "sid",
    "updated_at",
    "year",
    "visitor.id",
    "visitor.age",
    "visitor.sex"
)



Display Name: user_bbfa5ce0
Visotrs Path: dbfs:/tmp/user_bbfa5ce0/visitors.json
[Truncated to first 65536 bytes]
+------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+---------------------------------------------+
|county|created_at|first_name|id                                  |meta|name_count|position|sex|sid               |updated_at|year|parsed_visitors                              |
+------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+---------------------------------------------+
|KINGS |1574264158|ZOEY      |00000000-0000-0000-0838-60C2FFCC43AE|{ } |11        |0       |F  |row-r9pv-p86t.ifsp|1574264158|2007|[{9615, 68, F}, {1882, 34, M}, {5987, 23, M}]|
+------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+--------------------------------------------

In [0]:
df_visitors_flattened.show(140)

+-----------+----------+----------+--------------------+----+----------+--------+---+------------------+----------+----+----+---+---+
|     county|created_at|first_name|                  id|meta|name_count|position|sex|               sid|updated_at|year|  id|age|sex|
+-----------+----------+----------+--------------------+----+----------+--------+---+------------------+----------+----+----+---+---+
|      KINGS|1574264158|      ZOEY|00000000-0000-000...| { }|        11|       0|  F|row-r9pv-p86t.ifsp|1574264158|2007|9615| 68|  F|
|      KINGS|1574264158|      ZOEY|00000000-0000-000...| { }|        11|       0|  F|row-r9pv-p86t.ifsp|1574264158|2007|1882| 34|  M|
|      KINGS|1574264158|      ZOEY|00000000-0000-000...| { }|        11|       0|  F|row-r9pv-p86t.ifsp|1574264158|2007|5987| 23|  M|
|    SUFFOLK|1574264158|      ZOEY|00000000-0000-000...| { }|         6|       0|  F|row-7v2v~88z5-44se|1574264158|2007|3230| 45|  M|
|    SUFFOLK|1574264158|      ZOEY|00000000-0000-000...| { }| 

In [0]:
df_visitors_flattened.groupBy("county").agg(countDistinct("county").alias("distinct_counties")).show(1000)

+------------+-----------------+
|      county|distinct_counties|
+------------+-----------------+
|    FRANKLIN|                1|
|     STEUBEN|                1|
|      MONROE|                1|
|  LIVINGSTON|                1|
|    ONONDAGA|                1|
|    NEW YORK|                1|
|       KINGS|                1|
|      ALBANY|                1|
|       WAYNE|                1|
|     MADISON|                1|
|    RICHMOND|                1|
|      ORANGE|                1|
|      CAYUGA|                1|
|     SUFFOLK|                1|
|      OTSEGO|                1|
|      OSWEGO|                1|
|     CLINTON|                1|
|        ERIE|                1|
|      BROOME|                1|
|      GREENE|                1|
|    DELAWARE|                1|
|     NIAGARA|                1|
|     WYOMING|                1|
|  CHAUTAUQUA|                1|
|      ULSTER|                1|
|       TIOGA|                1|
|       YATES|                1|
|   SCHOHA

In [0]:
from pyspark.sql.functions import trim, upper

# Apply trim and convert to upper case, then create a new column
df_visitors_flattened = df_visitors_flattened.withColumn("county_trimmed_upper", upper(trim("county")))

# Show the result with the new column
df_visitors_flattened.show(1000)


+-----------+----------+----------+--------------------+----+----------+--------+---+------------------+----------+----+----+---+---+--------------------+
|     county|created_at|first_name|                  id|meta|name_count|position|sex|               sid|updated_at|year|  id|age|sex|county_trimmed_upper|
+-----------+----------+----------+--------------------+----+----------+--------+---+------------------+----------+----+----+---+---+--------------------+
|      KINGS|1574264158|      ZOEY|00000000-0000-000...| { }|        11|       0|  F|row-r9pv-p86t.ifsp|1574264158|2007|9615| 68|  F|               KINGS|
|      KINGS|1574264158|      ZOEY|00000000-0000-000...| { }|        11|       0|  F|row-r9pv-p86t.ifsp|1574264158|2007|1882| 34|  M|               KINGS|
|      KINGS|1574264158|      ZOEY|00000000-0000-000...| { }|        11|       0|  F|row-r9pv-p86t.ifsp|1574264158|2007|5987| 23|  M|               KINGS|
|    SUFFOLK|1574264158|      ZOEY|00000000-0000-000...| { }|         

In [0]:
df_visitors_flattened.select(col('county'),col('county_trimmed_upper')).show(100000)

+-----------+--------------------+
|     county|county_trimmed_upper|
+-----------+--------------------+
|      KINGS|               KINGS|
|      KINGS|               KINGS|
|      KINGS|               KINGS|
|    SUFFOLK|             SUFFOLK|
|    SUFFOLK|             SUFFOLK|
|     MONROE|              MONROE|
|       ERIE|                ERIE|
|     ULSTER|              ULSTER|
|     ULSTER|              ULSTER|
|     ULSTER|              ULSTER|
|WESTCHESTER|         WESTCHESTER|
|      BRONX|               BRONX|
|      BRONX|               BRONX|
|      BRONX|               BRONX|
|      BRONX|               BRONX|
|   NEW YORK|            NEW YORK|
|   NEW YORK|            NEW YORK|
|   NEW YORK|            NEW YORK|
|     NASSAU|              NASSAU|
|     NASSAU|              NASSAU|
|       ERIE|                ERIE|
|       ERIE|                ERIE|
|    SUFFOLK|             SUFFOLK|
|    SUFFOLK|             SUFFOLK|
|    SUFFOLK|             SUFFOLK|
|    SUFFOLK|       

In [0]:
# Filter and show rows where 'county' and 'county_trimmed_upper' are not equal
df_visitors_flattened.filter(col("county") != col("county_trimmed_upper")) \
    .select(col('county'), col('county_trimmed_upper')) \
    .show(100000, truncate=False)

+------------+--------------------+
|county      |county_trimmed_upper|
+------------+--------------------+
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY              |
|Albany      |ALBANY        

In [0]:
from pyspark.sql.functions import upper

# Normalize the case of the 'county' column
df_visitors_flattened = df_visitors_flattened.withColumn("county_normalized", upper(col("county")))

In [0]:
from pyspark.sql.functions import countDistinct, collect_set

df_grouped = df_visitors_flattened.groupBy("county_normalized").agg(
    countDistinct("county").alias("distinct_case_variations"),
    collect_set("county").alias("case_variations")
)

df_grouped.show(truncate=False)


+-----------------+------------------------+--------------------------+
|county_normalized|distinct_case_variations|case_variations           |
+-----------------+------------------------+--------------------------+
|FULTON           |2                       |[FULTON, Fulton]          |
|ST. LAWRENCE     |1                       |[St. Lawrence]            |
|CATTARAUGUS      |2                       |[Cattaraugus, CATTARAUGUS]|
|STEUBEN          |2                       |[Steuben, STEUBEN]        |
|YATES            |2                       |[YATES, Yates]            |
|KINGS            |2                       |[KINGS, Kings]            |
|OSWEGO           |2                       |[OSWEGO, Oswego]          |
|MADISON          |2                       |[Madison, MADISON]        |
|JEFFERSON        |2                       |[JEFFERSON, Jefferson]    |
|CHAUTAUQUA       |2                       |[Chautauqua, CHAUTAUQUA]  |
|SCHENECTADY      |2                       |[Schenectady, SCHENE

In [0]:
from pyspark.sql.functions import upper

# Normalize the case of the 'county' column
df_visitors_flattened = df_visitors_flattened.withColumn("first_name_normalized", upper(col("first_name")))

In [0]:
df_grouped = df_visitors_flattened.groupBy("first_name_normalized").agg(
    countDistinct("first_name").alias("distinct_case_variations"),
    collect_set("first_name").alias("case_variations")
)

df_grouped.show(100000,truncate=False)

+---------------------+------------------------+---------------+
|first_name_normalized|distinct_case_variations|case_variations|
+---------------------+------------------------+---------------+
|AADEN                |1                       |[AADEN]        |
|AAHIL                |1                       |[AAHIL]        |
|AALIYAH              |1                       |[AALIYAH]      |
|AARAV                |1                       |[AARAV]        |
|AARIZ                |1                       |[AARIZ]        |
|AARON                |1                       |[AARON]        |
|AARYA                |1                       |[AARYA]        |
|AAYAN                |1                       |[AAYAN]        |
|ABBA                 |1                       |[ABBA]         |
|ABBY                 |1                       |[ABBY]         |
|ABDIEL               |1                       |[ABDIEL]       |
|ABDOUL               |1                       |[ABDOUL]       |
|ABDOULAYE            |1 

In [0]:
# Filter to show only records with more than one distinct case variation
df_case_variations = df_grouped.filter(col("distinct_case_variations") > 1)

df_case_variations.show(100000, truncate=False)

+---------------------+------------------------+---------------+
|first_name_normalized|distinct_case_variations|case_variations|
+---------------------+------------------------+---------------+
+---------------------+------------------------+---------------+



In [0]:
from pyspark.sql.functions import upper

# Normalize the case of the 'county' column
df_visitors_flattened = df_visitors_flattened.withColumn("sex_normalized", upper(col("sex")))

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-3155276111774480>, line 4
      1 from pyspark.sql.functions import upper
      3 # Normalize the case of the 'county' column
----> 4 df_visitors_flattened = df_visitors_flattened.withColumn("sex_normalized", upper(col("sex")))

File /databricks/spark/python/pyspark/instrumentation_utils.py:47, in _wrap_function.<locals>.wrapper(*args, **kwargs)
     45 start = time.perf_counter()
     46 try:
---> 47     res = func(*args, **kwargs)
     48     logger.log_success(
     49         module_name, class_name, function_name, time.perf_counter() - start, signature
     50     )
     51     return res

File /databricks/spark/python/pyspark/sql/dataframe.py:5932, in DataFrame.withColumn(self, colName, col)
   5927 if not isinstance(col, Column):
   5928     raise PySparkTypeError(
   5929         error_class="NOT_COLUMN",
   5930  

In [0]:
from pyspark.sql.functions import upper, col

# Normalize the case of the 'sex' column in df_visitors_flattened
df_visitors_flattened = df_visitors_flattened.withColumn("sex_normalized", upper(col('sex')))

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-3155276111774492>, line 4
      1 from pyspark.sql.functions import upper, col
      3 # Normalize the case of the 'sex' column in df_visitors_flattened
----> 4 df_visitors_flattened = df_visitors_flattened.withColumn("sex_normalized", upper(col('sex')))

File /databricks/spark/python/pyspark/instrumentation_utils.py:47, in _wrap_function.<locals>.wrapper(*args, **kwargs)
     45 start = time.perf_counter()
     46 try:
---> 47     res = func(*args, **kwargs)
     48     logger.log_success(
     49         module_name, class_name, function_name, time.perf_counter() - start, signature
     50     )
     51     return res

File /databricks/spark/python/pyspark/sql/dataframe.py:5932, in DataFrame.withColumn(self, colName, col)
   5927 if not isinstance(col, Column):
   5928     raise PySparkTypeError(
   5929         error_cl

In [0]:
df_visitors_flattened.show()

+-----------+----------+----------+--------------------+----+----------+--------+---+------------------+----------+----+----+---+---+--------------------+-----------------+---------------------+
|     county|created_at|first_name|                  id|meta|name_count|position|sex|               sid|updated_at|year|  id|age|sex|county_trimmed_upper|county_normalized|first_name_normalized|
+-----------+----------+----------+--------------------+----+----------+--------+---+------------------+----------+----+----+---+---+--------------------+-----------------+---------------------+
|      KINGS|1574264158|      ZOEY|00000000-0000-000...| { }|        11|       0|  F|row-r9pv-p86t.ifsp|1574264158|2007|9615| 68|  F|               KINGS|            KINGS|                 ZOEY|
|      KINGS|1574264158|      ZOEY|00000000-0000-000...| { }|        11|       0|  F|row-r9pv-p86t.ifsp|1574264158|2007|1882| 34|  M|               KINGS|            KINGS|                 ZOEY|
|      KINGS|1574264158| 

In [0]:
# https://docs.python.org/3/library/hashlib.html#blake2
from hashlib import blake2b

user = dbutils.notebook.entry_point.getDbutils().notebook().getContext().tags().apply('user')
h = blake2b(digest_size=4)
h.update(user.encode("utf-8"))
display_name = "user_" + h.hexdigest()
print("Display Name: " + display_name)

dbutils.fs.cp('file:/tmp/visitors.json',f"dbfs:/tmp/{display_name}/visitors.json")
visitors_path = f"dbfs:/tmp/{display_name}/visitors.json"

print("Visotrs Path: " + visitors_path)
dbutils.fs.head(visitors_path)


df_visitors = spark.read.option("inferSchema", True).json(visitors_path)


import xml.etree.ElementTree as ET
from pyspark.sql.functions import udf
from pyspark.sql.types import StringType, StructType, StructField  # Import additional types as needed

def parse_visitors(xml_data):
    if xml_data is None or xml_data.strip() == '':
        return []

    try:
        visitors = []
        root = ET.fromstring(xml_data)

        for visitor in root.findall('visitor'):
            visitor_id = visitor.get('id')
            visitor_age = int(visitor.get('age')) if visitor.get('age') is not None else None
            visitor_sex = visitor.get('sex')

            visitors.append((visitor_id, visitor_age, visitor_sex))

        return visitors
    except ET.ParseError:
        return []  # Return empty list in case of parsing error

# Define the schema for the visitor information
visitor_schema = ArrayType(StructType([
    StructField("id", StringType(), True),
    StructField("age", IntegerType(), True),
    StructField("sex", StringType(), True)
]))

# Register the UDF
parse_visitors_udf = udf(parse_visitors, visitor_schema)


df_visitors_transformed = df_visitors.withColumn("parsed_visitors", parse_visitors_udf(df_visitors["visitors"]))


df_visitors_transformed.select('county','created_at','first_name','id','meta','name_count','position','sex','sid','updated_at','year','parsed_visitors').limit(1).show(truncate=False)


df_visitors_flattened = df_visitors_transformed.withColumn("visitor", explode("parsed_visitors"))


df_visitors_flattened = df_visitors_flattened.select(
    col("county"),
    col("created_at"),
    col("first_name"),
    col("id"),
    col("meta"),
    col("name_count"),
    col("position"),
    col("sex"),
    col("sid"),
    col("updated_at"),
    col("year"),
    col("visitor.id").alias("visitor_id"),
    col("visitor.age").alias("visitor_age"),
    col("visitor.sex").alias("visitor_sex")
)



Display Name: user_bbfa5ce0
Visotrs Path: dbfs:/tmp/user_bbfa5ce0/visitors.json
[Truncated to first 65536 bytes]
+------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+---------------------------------------------+
|county|created_at|first_name|id                                  |meta|name_count|position|sex|sid               |updated_at|year|parsed_visitors                              |
+------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+---------------------------------------------+
|KINGS |1574264158|ZOEY      |00000000-0000-0000-0838-60C2FFCC43AE|{ } |11        |0       |F  |row-r9pv-p86t.ifsp|1574264158|2007|[{9615, 68, F}, {1882, 34, M}, {5987, 23, M}]|
+------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+--------------------------------------------

In [0]:
df_visitors_flattened.show()

+-----------+----------+----------+--------------------+----+----------+--------+---+------------------+----------+----+----------+-----------+-----------+
|     county|created_at|first_name|                  id|meta|name_count|position|sex|               sid|updated_at|year|visitor_id|visitor_age|visitor_sex|
+-----------+----------+----------+--------------------+----+----------+--------+---+------------------+----------+----+----------+-----------+-----------+
|      KINGS|1574264158|      ZOEY|00000000-0000-000...| { }|        11|       0|  F|row-r9pv-p86t.ifsp|1574264158|2007|      9615|         68|          F|
|      KINGS|1574264158|      ZOEY|00000000-0000-000...| { }|        11|       0|  F|row-r9pv-p86t.ifsp|1574264158|2007|      1882|         34|          M|
|      KINGS|1574264158|      ZOEY|00000000-0000-000...| { }|        11|       0|  F|row-r9pv-p86t.ifsp|1574264158|2007|      5987|         23|          M|
|    SUFFOLK|1574264158|      ZOEY|00000000-0000-000...| { }|   

In [0]:
df_visitors_flattened = df_visitors_transformed.withColumn("visitor", explode("parsed_visitors"))

In [0]:
df_visitors_flattened.show()

+-----------+----------+----------+--------------------+----+----------+--------+---+------------------+----------+--------------------+----+--------------------+-------------+
|     county|created_at|first_name|                  id|meta|name_count|position|sex|               sid|updated_at|            visitors|year|     parsed_visitors|      visitor|
+-----------+----------+----------+--------------------+----+----------+--------+---+------------------+----------+--------------------+----+--------------------+-------------+
|      KINGS|1574264158|      ZOEY|00000000-0000-000...| { }|        11|       0|  F|row-r9pv-p86t.ifsp|1574264158|<?xml version="1....|2007|[{9615, 68, F}, {...|{9615, 68, F}|
|      KINGS|1574264158|      ZOEY|00000000-0000-000...| { }|        11|       0|  F|row-r9pv-p86t.ifsp|1574264158|<?xml version="1....|2007|[{9615, 68, F}, {...|{1882, 34, M}|
|      KINGS|1574264158|      ZOEY|00000000-0000-000...| { }|        11|       0|  F|row-r9pv-p86t.ifsp|1574264158|

In [0]:
df_visitors_flattened = df_visitors_flattened.select(
    col("county"),
    col("created_at"),
    col("first_name"),
    col("id"),
    col("meta"),
    col("name_count"),
    col("position"),
    col("sex"),
    col("sid"),
    col("updated_at"),
    col("year"),
    col("visitor.id").alias("visitor_id"),
    col("visitor.age").alias("visitor_age"),
    col("visitor.sex").alias("visitor_sex")
)

In [0]:
df_visitors_flattened.show()

+-----------+----------+----------+--------------------+----+----------+--------+---+------------------+----------+----+----------+-----------+-----------+
|     county|created_at|first_name|                  id|meta|name_count|position|sex|               sid|updated_at|year|visitor_id|visitor_age|visitor_sex|
+-----------+----------+----------+--------------------+----+----------+--------+---+------------------+----------+----+----------+-----------+-----------+
|      KINGS|1574264158|      ZOEY|00000000-0000-000...| { }|        11|       0|  F|row-r9pv-p86t.ifsp|1574264158|2007|      9615|         68|          F|
|      KINGS|1574264158|      ZOEY|00000000-0000-000...| { }|        11|       0|  F|row-r9pv-p86t.ifsp|1574264158|2007|      1882|         34|          M|
|      KINGS|1574264158|      ZOEY|00000000-0000-000...| { }|        11|       0|  F|row-r9pv-p86t.ifsp|1574264158|2007|      5987|         23|          M|
|    SUFFOLK|1574264158|      ZOEY|00000000-0000-000...| { }|   

In [0]:
# Filter the DataFrame for first_name 'ZOEY' and year 2007
filtered_df = df_visitors_flattened.filter((df_visitors_flattened['first_name'] == 'ZOEY') & (df_visitors_flattened['year'] == 2007))

# Show the result
filtered_df.show(truncate=False)


+-------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+----------+-----------+-----------+
|county |created_at|first_name|id                                  |meta|name_count|position|sex|sid               |updated_at|year|visitor_id|visitor_age|visitor_sex|
+-------+----------+----------+------------------------------------+----+----------+--------+---+------------------+----------+----+----------+-----------+-----------+
|KINGS  |1574264158|ZOEY      |00000000-0000-0000-0838-60C2FFCC43AE|{ } |11        |0       |F  |row-r9pv-p86t.ifsp|1574264158|2007|9615      |68         |F          |
|KINGS  |1574264158|ZOEY      |00000000-0000-0000-0838-60C2FFCC43AE|{ } |11        |0       |F  |row-r9pv-p86t.ifsp|1574264158|2007|1882      |34         |M          |
|KINGS  |1574264158|ZOEY      |00000000-0000-0000-0838-60C2FFCC43AE|{ } |11        |0       |F  |row-r9pv-p86t.ifsp|1574264158|2007|5987      |23         |M    

In [0]:
from pyspark.sql.functions import upper

# Normalize the case of the 'county' column
df_visitors_flattened = df_visitors_flattened.withColumn("sex_normalized", upper(col("visitor_sex")))

In [0]:
from pyspark.sql.functions import upper, col

# Normalize the case of the 'sex' column in df_visitors_flattened
df_visitors_flattened = df_visitors_flattened.withColumn("sex_normalized", upper(col('visitor_sex')))

In [0]:
df_grouped = df_visitors_flattened.groupBy("sex_normalized").agg(
    countDistinct("visitor_sex").alias("distinct_case_variations"),
    collect_set("visitor_sex").alias("case_variations")
)

df_grouped.show(truncate=False)

+--------------+------------------------+---------------+
|sex_normalized|distinct_case_variations|case_variations|
+--------------+------------------------+---------------+
|F             |1                       |[F]            |
|M             |1                       |[M]            |
+--------------+------------------------+---------------+



In [0]:
# Filter and show rows where 'county' and 'county_trimmed_upper' are not equal
df_visitors_flattened.filter(col("sex") != col("sex_normalized")) \
    .select(col('visitor_sex'), col('sex_normalized')) \
    .show(100000, truncate=False)

+-----------+--------------+
|visitor_sex|sex_normalized|
+-----------+--------------+
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|M          |M             |
|F          |F             |
|F          |F             |
|F          |F             |
|F          |F             |
|M          |M             |
|M          |M             |
|F          |F             |
|F          |F

In [0]:
df_visitors_flattened.printSchema()

root
 |-- county: string (nullable = true)
 |-- created_at: string (nullable = true)
 |-- first_name: string (nullable = true)
 |-- id: string (nullable = true)
 |-- meta: string (nullable = true)
 |-- name_count: string (nullable = true)
 |-- position: string (nullable = true)
 |-- sex: string (nullable = true)
 |-- sid: string (nullable = true)
 |-- updated_at: string (nullable = true)
 |-- year: string (nullable = true)
 |-- visitor_id: string (nullable = true)
 |-- visitor_age: integer (nullable = true)
 |-- visitor_sex: string (nullable = true)
 |-- sex_normalized: string (nullable = true)



In [0]:
display(df_visitors_flattened)

county created_at first_name id meta name_count position sex sid updated_at year visitor_id visitor_age visitor_sex sex_normalized KINGS 1574264158 ZOEY 00000000-0000-0000-0838-60C2FFCC43AE { } 11 0 F row-r9pv-p86t.ifsp 1574264158 2007 9615 68 F F KINGS 1574264158 ZOEY 00000000-0000-0000-0838-60C2FFCC43AE { } 11 0 F row-r9pv-p86t.ifsp 1574264158 2007 1882 34 M M KINGS 1574264158 ZOEY 00000000-0000-0000-0838-60C2FFCC43AE { } 11 0 F row-r9pv-p86t.ifsp 1574264158 2007 5987 23 M M SUFFOLK 1574264158 ZOEY 00000000-0000-0000-C8FC-DDD3F9A72DFF { } 6 0 F row-7v2v~88z5-44se 1574264158 2007 3230 45 M M SUFFOLK 1574264158 ZOEY 00000000-0000-0000-C8FC-DDD3F9A72DFF { } 6 0 F row-7v2v~88z5-44se 1574264158 2007 5243 44 M M MONROE 1574264158 ZOEY 00000000-0000-0000-562E-D9A0792557FC { } 6 0 F row-hzc9-4kvv~mbc9 1574264158 2007 8631 8 M M ERIE 1574264158 ZOEY 00000000-0000-0000-B19D-7B88FF2FB6A0 { } 9 0 F row-3473_8cwy~3vez 1574264158 2007 5233 57 M M ULSTER 1574264158 ZOE 00000000-0000-0000-7D66-E7EC8F12BB8D { } 5 0 F row-tyuh.nmy9.r2n3 1574264158 2007 7108 58 M M ULSTER 1574264158 ZOE 00000000-0000-0000-7D66-E7EC8F12BB8D { } 5 0 F row-tyuh.nmy9.r2n3 1574264158 2007 7555 29 M M ULSTER 1574264158 ZOE 00000000-0000-0000-7D66-E7EC8F12BB8D { } 5 0 F row-tyuh.nmy9.r2n3 1574264158 2007 3949 44 F F WESTCHESTER 1574264158 ZOE 00000000-0000-0000-7ECC-F350540A8F92 { } 24 0 F row-ct48~ui69-2zsn 1574264158 2007 667 9 M M BRONX 1574264158 ZOE 00000000-0000-0000-30FB-CB5E36017AD5 { } 13 0 F row-gdva~4v8k-vuwy 1574264158 2007 8199 14 M M BRONX 1574264158 ZOE 00000000-0000-0000-30FB-CB5E36017AD5 { } 13 0 F row-gdva~4v8k-vuwy 1574264158 2007 7545 34 M M BRONX 1574264158 ZOE 00000000-0000-0000-30FB-CB5E36017AD5 { } 13 0 F row-gdva~4v8k-vuwy 1574264158 2007 617 1 F F BRONX 1574264158 ZOE 00000000-0000-0000-30FB-CB5E36017AD5 { } 13 0 F row-gdva~4v8k-vuwy 1574264158 2007 1442 49 F F NEW YORK 1574264158 ZOE 00000000-0000-0000-E380-AAAB1FA5C7A7 { } 55 0 F row-gzu3~a7hk~bqym 1574264158 2007 3890 13 F F NEW YORK 1574264158 ZOE 00000000-0000-0000-E380-AAAB1FA5C7A7 { } 55 0 F row-gzu3~a7hk~bqym 1574264158 2007 5965 30 M M NEW YORK 1574264158 ZOE 00000000-0000-0000-E380-AAAB1FA5C7A7 { } 55 0 F row-gzu3~a7hk~bqym 1574264158 2007 9770 42 F F NASSAU 1574264158 ZOE 00000000-0000-0000-A7FF-8A4260B3A505 { } 15 0 F row-ekbw_tb7c.yvgp 1574264158 2007 2286 50 M M NASSAU 1574264158 ZOE 00000000-0000-0000-A7FF-8A4260B3A505 { } 15 0 F row-ekbw_tb7c.yvgp 1574264158 2007 1809 53 M M ERIE 1574264158 ZOE 00000000-0000-0000-3F7C-4DECA15E0F5B { } 6 0 F row-zk7s-r2ma_t8mk 1574264158 2007 3354 61 M M ERIE 1574264158 ZOE 00000000-0000-0000-3F7C-4DECA15E0F5B { } 6 0 F row-zk7s-r2ma_t8mk 1574264158 2007 2266 34 M M SUFFOLK 1574264158 ZOE 00000000-0000-0000-854E-D29D5B4D5636 { } 14 0 F row-ieja_864x~w2ki 1574264158 2007 6920 46 F F SUFFOLK 1574264158 ZOE 00000000-0000-0000-854E-D29D5B4D5636 { } 14 0 F row-ieja_864x~w2ki 1574264158 2007 3318 1 F F SUFFOLK 1574264158 ZOE 00000000-0000-0000-854E-D29D5B4D5636 { } 14 0 F row-ieja_864x~w2ki 1574264158 2007 8332 57 F F SUFFOLK 1574264158 ZOE 00000000-0000-0000-854E-D29D5B4D5636 { } 14 0 F row-ieja_864x~w2ki 1574264158 2007 5027 51 M M KINGS 1574264158 ZOE 00000000-0000-0000-C177-43F52BFECC07 { } 34 0 F row-8fp4.rjtj.h46h 1574264158 2007 48 38 M M MONROE 1574264158 ZOE 00000000-0000-0000-CF24-5370794D0031 { } 9 0 F row-4ips.rj88_zm5z 1574264158 2007 4540 34 F F MONROE 1574264158 ZOE 00000000-0000-0000-CF24-5370794D0031 { } 9 0 F row-4ips.rj88_zm5z 1574264158 2007 816 17 F F QUEENS 1574264158 ZOE 00000000-0000-0000-D604-3405BD7A5CC9 { } 26 0 F row-7unr-77py~g5na 1574264158 2007 7585 31 F F QUEENS 1574264158 ZOE 00000000-0000-0000-D604-3405BD7A5CC9 { } 26 0 F row-7unr-77py~g5na 1574264158 2007 977 54 F F QUEENS 1574264158 ZOE 00000000-0000-0000-D604-3405BD7A5CC9 { } 26 0 F row-7unr-77py~g5na 1574264158 2007 2001 34 F F QUEENS 1574264158 ZOE 00000000-0000-0000-D604-3405BD7A5CC9 { } 26 0 F row-7unr-77py~g5na 1574264158 2007 3586 64 F F ALBANY 1574264158 Z